Import packages needed

In [19]:
import suite2p
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import os
import glob
from natsort import natsorted
from multiprocessing import Pool
from joblib import Parallel, delayed
from pathlib import Path
import gc
gc.collect()
import importlib
import sys
from pathlib import Path
# Add the directory containing your script to the Python path
sys.path.append(r'C:\Users\User\Project-SLMonlineControl\CodeAndPackages\PYsubfun')
#sys.path.append(r'C:\Users\zhangl33\Projects\Project-SLMonlineControl\CodeAndPackages\PYsubfun')

# Now you can import your script as a module
import FastBin_Suite2p as FBS
import CalBin2p as CB
import SLM_Offline as slmO
import Suite2p_QualityControl as QC 

In [3]:
#importlib.reload(FBS)
# Pre-set parameters, and load the only bin files in the pre-set path folde
ConfigFolder=r'C:\Users\User\Project-SLMonlineControl\config'
#ConfigFolder=r'C:\Users\zhangl33\Projects\Project-SLMonlineControl\config'
ops0, confSet=FBS.configLoad(ConfigFolder,'SLMsetting.yml','ops3Planes.npy')
SaveFolder=FBS.suite2pInitiate(ops0,ConfigFolder)
binFile = glob.glob(ops0['save_path0'] + '/TSeries*-001.bin')    ##<<<<<<<<<<<<<<<<<<<<<<<<<< Noted that there supposed be only one Bin Data file
#Load Data
print(binFile)
rawBin, FramePerPlane, TotalFrameNeed=FBS.LoadBin(binFile,ops0)
rawBin.shape

Processed data would be saved inE:\LuSLMOnlineTest\L00121\09232025\suite2p
File found: C:\Users\User\Project-SLMonlineControl\config\SLMsetting.yml
Copying to: E:\LuSLMOnlineTest\L00121\09232025\CurrentSLMsetting.yml
Current SLMsetting copied successfully!
['E:\\LuSLMOnlineTest\\L00121\\09232025\\TSeries-09232025-0903-001.bin']


(24600, 512, 512)

In [4]:
ops0['spatial_scale']=2
ops0['threshold_scaling']=1.6
ops0['denoise']=1

ops0

{'suite2p_version': '0.14.2.dev17+gf3d7d4e',
 'look_one_level_down': 1.0,
 'fast_disk': [],
 'delete_bin': False,
 'mesoscan': False,
 'bruker': False,
 'bruker_bidirectional': False,
 'h5py': [],
 'h5py_key': 'data',
 'nwb_file': '',
 'nwb_driver': '',
 'nwb_series': '',
 'save_path0': 'E:\\LuSLMOnlineTest\\L00121\\09232025\\',
 'save_folder': [],
 'subfolders': [],
 'move_bin': False,
 'nplanes': 3,
 'nchannels': 1,
 'functional_chan': 1,
 'tau': 1.5,
 'fs': 6.9,
 'force_sktiff': False,
 'frames_include': -1,
 'multiplane_parallel': 0.0,
 'ignore_flyback': [],
 'preclassify': 0.0,
 'save_mat': True,
 'save_NWB': 0.0,
 'combined': 1.0,
 'aspect': 1.0,
 'do_bidiphase': False,
 'bidiphase': 0.0,
 'bidi_corrected': False,
 'do_registration': 1,
 'two_step_registration': 0.0,
 'keep_movie_raw': False,
 'nimg_init': 300,
 'batch_size': 500,
 'maxregshift': 0.1,
 'align_by_chan': 1,
 'reg_tif': True,
 'reg_tif_chan2': False,
 'subpixel': 10,
 'smooth_sigma_time': 0.0,
 'smooth_sigma': 1.15,

Suite2p processing with no motion correction; Noted following defining a function to process a plane of data; Next session, parallel processing for each plane is excuted. Much time is saved. 
Alternatively, run this process with Step2-OnlineBinSuite2p.ipynb

In [5]:
# Define the number of parallel processes; 
# Noted that current binning movie in chuns of length 06; increase this parameter could decrease the number of frames within a chunks, using less memory
num_processes=1              ## <<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<<
# Create a list of plane indices
plane_indices = range(0,ops0['nplanes'])
print(plane_indices)
ops1=ops0
Parallel(n_jobs=num_processes)(delayed(FBS.process_plane)(plane_idx, rawBin, SaveFolder, ops1) for plane_idx in plane_indices)

# Combine multiple plane data
#FBS.CombinePlanes(SaveFolder,ops0)
FBS.CombinePlanes(SaveFolder,ops0)

range(0, 3)
Processing plane 0
Binning movie in chunks of length 10
Binned movie of size [820,512,512] created in 7.37 sec.
Binned movie denoised (for cell detection only) in 17.57 sec.
NOTE: FORCED spatial scale ~12 pixels, time epochs 1.00, threshold 16.00 
0 ROIs, score=177.73
Detected 260 ROIs, 17.32 sec
After removing overlaps, 260 ROIs remain
added enhanced mean image
Masks created, 0.86 sec.


c:\users\user\suite2p\suite2p\extraction\extract.py:125: NumbaTypeSafetyWarning: unsafe cast from uint64 to int64. Precision may be lost.
  Fi[n] = np.dot(data[:, cell_ipix[n]], cell_lam[n])


Extracted fluorescence from 260 ROIs in 8200 frames, 16.66 sec.
Extracted fluorescence from 260 ROIs in 8200 frames, 11.37 sec.
['npix_norm', 'compact', 'skew']
Processing plane 1
Binning movie in chunks of length 10
Binned movie of size [820,512,512] created in 7.81 sec.
Binned movie denoised (for cell detection only) in 16.83 sec.
NOTE: FORCED spatial scale ~12 pixels, time epochs 1.00, threshold 16.00 
0 ROIs, score=217.13
Detected 222 ROIs, 16.49 sec
After removing overlaps, 219 ROIs remain
added enhanced mean image
Masks created, 0.74 sec.
Extracted fluorescence from 219 ROIs in 8200 frames, 11.04 sec.
Extracted fluorescence from 219 ROIs in 8200 frames, 11.09 sec.
['npix_norm', 'compact', 'skew']
Processing plane 2
Binning movie in chunks of length 10
Binned movie of size [820,512,512] created in 8.03 sec.
Binned movie denoised (for cell detection only) in 16.93 sec.
NOTE: FORCED spatial scale ~12 pixels, time epochs 1.00, threshold 16.00 
0 ROIs, score=197.99
Detected 159 ROIs, 

Run Suite2p gui from command line, load combined data above, do necessary mannual correction. Saved the data.

Once above mannual correction is done; update the result in each plane

In [23]:
suite2pdir=os.path.join(r'E:\LuSLMOnlineTest\L00121\09232025','suite2p')
suite2pdir=os.path.join(ops0["save_path0"],'suite2p')
print(suite2pdir)
combinedPath=os.path.join(suite2pdir,'combined')
print(combinedPath)

E:\LuSLMOnlineTest\L00121\09232025\suite2p
E:\LuSLMOnlineTest\L00121\09232025\suite2p\combined


In [25]:
slmO.backup_iscell_npy(suite2pdir)

[WindowsPath('E:/LuSLMOnlineTest/L00121/09232025/suite2p/combined/iscellRaw.npy'),
 WindowsPath('E:/LuSLMOnlineTest/L00121/09232025/suite2p/plane0/iscellRaw.npy'),
 WindowsPath('E:/LuSLMOnlineTest/L00121/09232025/suite2p/plane1/iscellRaw.npy'),
 WindowsPath('E:/LuSLMOnlineTest/L00121/09232025/suite2p/plane2/iscellRaw.npy')]

In [27]:
importlib.reload(QC)

<module 'Suite2p_QualityControl' from 'C:\\Users\\zhangl33\\Projects\\Project-SLMonlineControl\\CodeAndPackages\\PYsubfun\\Suite2p_QualityControl.py'>

In [54]:
DEFAULT_PARAMS = {
    "nperseg": 512,
    "low_band": (0.2, 1.6),
    "high_band": (2.5, 3.3),
    "amp_method": "sum",
    "min_event_snr": 4,
    "amp_percentile": 0.5,
    "eps": 20,
    "recompute_spks": True,
}
params = {**DEFAULT_PARAMS, "low_band": (0.2, 1.6), "high_band": (2.5, 3.3)}
df_metrics, psdPerc, fre = QC.suite2pMetric(combinedPath, params)


6.9
0.7
60.0
20.0


In [57]:
# Step 1: Build the condition (boolean mask)
iscell_update = df_metrics['iscell'].to_numpy()
mask = (
    (df_metrics['footprint'] > 0.1) &
    (df_metrics['snr_oasis_evt'] > 1) &
    (df_metrics['mrs0'] > 2.5) &
    (df_metrics['compact'] < 1.1)&
    (df_metrics['iscell'] > 0)
)

# Step 2: Use np.where to get indices (like MATLAB find)
iscell_update = np.where(mask)[0]

print(iscell_update)  # e.g. [2 5 7]


[  0   1   2   3   4   5   6   7   8   9  10  11  12  13  14  15  16  17
  18  19  20  21  22  23  24  25  26  27  28  29  30  31  32  33  34  35
  36  37  38  39  40  41  42  43  44  45  46  47  48  49  50  51  53  54
  55  56  57  58  59  60  61  62  64  65  66  67  68  69  70  71  72  73
  74  76  77  78  79  80  81  82  83  84  85  86  87  88  89  90  91  92
  93  94  95  96  97  98  99 101 102 103 104 105 106 107 108 109 110 112
 113 115 117 118 120 121 122 123 124 127 130 131 133 134 135 140 141 142
 144 145 146 148 149 150 151 152 153 155 157 159 160 162 163 164 165 167
 168 169 170 173 177 182 188 189 190 191 192 195 196 198 199 203 207 208
 210 213 215 217 231 237 238 240 247 253 257 260 261 262 263 264 265 267
 268 269 270 271 273 274 275 276 278 280 281 282 283 284 285 286 287 288
 289 290 291 292 294 295 296 297 299 300 301 302 303 304 305 306 307 308
 309 310 311 312 313 314 316 317 321 322 323 324 325 326 327 328 329 330
 331 332 333 334 335 337 338 339 340 341 342 343 34

In [58]:




slmO.update_iscell(suite2pdir,iscell_update,3)


(638, 2)
(371,)
638 units total — 371 flagged as cells in combined data


(array([[1.        , 0.82354465],
        [1.        , 0.90915617],
        [1.        , 0.91355213],
        ...,
        [0.        , 0.47117257],
        [0.        , 0.747597  ],
        [1.        , 0.81301754]]),
 array([{'ypix': array([267, 267, 268, 269, 269, 269, 269, 269, 270, 270, 270, 270, 270,
               271, 271, 271, 271, 271, 271, 271, 271, 272, 272, 272, 272, 272,
               272, 272, 273, 273, 273, 273, 273, 273, 273, 273, 273, 274, 274,
               274, 274, 274, 274, 274, 274, 274, 274, 275, 275, 275, 275, 275,
               275, 275, 275, 275, 275, 275, 276, 276, 276, 276, 276, 276, 276,
               276, 276, 276, 277, 277, 277, 277, 277, 277, 277, 277, 277, 278,
               278, 278, 278, 278, 278, 278, 279, 279, 279, 279]), 'xpix': array([253, 254, 253, 252, 253, 254, 255, 256, 252, 253, 254, 255, 256,
               250, 251, 252, 253, 254, 255, 256, 257, 251, 252, 253, 254, 255,
               256, 257, 250, 251, 252, 253, 254, 255, 256, 257, 

In [59]:
FBS.PostMannual(SaveFolder,ops0)

NameError: name 'SaveFolder' is not defined